In [292]:
import numpy as np
import matplotlib.pyplot as plt

In [293]:
from loaders import clean_text_for_pattern_letter
from temp_text_puh import template_str
# input_str = clean_text_for_pattern_letter(template_str, out_len=len(template_str))
input_str = clean_text_for_pattern_letter(template_str, out_len=5000)
print(len(input_str))
letters = ['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u',
               'v', 'w', 'x', 'y', 'z', ' ', '.', ',', '"', '\'', '1']
print(f'{letters=}')

len(letters)=32
5000
letters=['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', ' ', '.', ',', '"', "'", '1']


In [294]:
def predict_train(input_str,
                  letters,
                  max_history=4,
                  max_index: int = 4,):
    WIN: dict[str, dict[str, int]] = {}

    HistoryHW: list[dict[str, int]] = []
    HistoryW: list[dict[str, dict[str, dict[int, int]]]] = []

    for h_idx in range(max_history):
        HistoryHW.append({})
        HistoryW.append({})

    IDX: list = []

    for letter in letters:
        WIN.setdefault(letter, {})

        for idx in range(max_index):
            WIN[letter].setdefault(idx, 0)

    prev_indices = [0]

    for inp_idx, inp in enumerate(input_str):
        if inp_idx <= 0:
            WIN[inp][prev_indices[0]] += 1
            continue

        IDX.append(prev_indices[0])

        IdxO = {}

        for h_idx in range(max_history):
            prev_idx = inp_idx - 1 - h_idx
            if prev_idx < 0:
                break

            prev_inp = input_str[prev_idx]

            HW = HistoryHW[h_idx]
            W = HistoryW[h_idx]

            key_HW = prev_inp + str(prev_indices[h_idx]) + ':' + inp

            if HW.get(key_HW, -1) != -1:
                inp_has_index = HW[key_HW]

                # idx_strength = W[prev_inp + str(prev_indices[h_idx])][inp][inp_has_index]

                IdxO.setdefault(inp_has_index, 0)
                IdxO[inp_has_index] += 1

        new_index = 0
        if len(IdxO) == 0:
            new_index = min(WIN[inp], key=WIN[inp].get)
        else:
            new_index = max(IdxO, key=IdxO.get)
        WIN[inp][new_index] += 1

        for h_idx in range(max_history):
            prev_idx = inp_idx - 1 - h_idx
            if prev_idx < 0:
                break

            prev_inp = input_str[prev_idx]

            key_I = prev_inp + str(prev_indices[h_idx])
            HistoryW[h_idx].setdefault(key_I, {})
            HistoryW[h_idx][key_I].setdefault(inp, {})
            HistoryW[h_idx][key_I][inp].setdefault(new_index, 0)
            HistoryW[h_idx][key_I][inp][new_index] += 1

            key_HW = prev_inp + str(prev_indices[h_idx]) + ':' + inp

            HistoryHW[h_idx].setdefault(key_HW, new_index)

        # recurtion
        prev_indices.insert(0, new_index)
        if len(prev_indices) > max_history:
            prev_indices = prev_indices[:-1]

    return HistoryW, HistoryHW, IDX

max_index_L1 = 32*2
max_history_L1 = 12

max_history_L1_ds = 11

HistoryW, HistoryHW, IDX = predict_train(input_str, letters, max_history=max_history_L1, max_index=max_index_L1)

for h_idx in range(max_history_L1):
    print(f'{h_idx=}')
    for wk, wv in HistoryW[h_idx].items():
        print(wk, wv)


h_idx=0
c0 {'h': {0: 1}}
h0 {'a': {0: 1}}
a0 {'p': {0: 1}}
p0 {'t': {0: 1}}
t0 {'e': {0: 1}}
e0 {'r': {0: 4}, 'c': {17: 1}, ' ': {30: 2, 33: 1}, 'l': {21: 1, 17: 1}}
r0 {' ': {0: 3}, 'e': {44: 1}}
 0 {'i': {0: 2}, 'f': {5: 1}, 'b': {14: 1}, 't': {51: 1}}
i0 {'n': {0: 1}, 't': {54: 1}}
n0 {' ': {1: 1}}
 1 {'w': {0: 2}, 'a': {18: 1}, 'y': {11: 1}}
w0 {'h': {1: 1}, 'i': {10: 1}}
h1 {'i': {1: 1}}
i1 {'c': {1: 1}}
c1 {'h': {2: 1}}
h2 {' ': {2: 1}}
 2 {'w': {1: 1}, 'm': {9: 1}, 's': {30: 1}}
w1 {'e': {1: 1}}
e1 {' ': {3: 1, 37: 2}, 's': {22: 2}}
 3 {'a': {1: 1}, 'o': {25: 1}, 'h': {37: 1}}
a1 {'r': {1: 1}, 'n': {1: 1}}
r1 {'e': {2: 1}}
e2 {' ': {4: 1}, 'l': {14: 1}}
 4 {'i': {2: 1}, 'a': {1: 1}, 't': {20: 1}}
i2 {'n': {1: 1}}
n1 {'t': {1: 1}, 'd': {11: 1}}
t1 {'r': {2: 1}}
r2 {'o': {0: 1}}
o0 {'d': {0: 1}}
d0 {'u': {0: 1}}
u0 {'c': {2: 1}}
c2 {'e': {3: 1}}
e3 {'d': {1: 2}}
d1 {' ': {5: 1, 30: 1}}
 5 {'t': {2: 1}, 'i': {23: 1}, 'w': {15: 1}}
t2 {'o': {1: 1}}
o1 {' ': {6: 1}}
 6 {'w': {2: 1}, 

In [295]:
def to_probability(HistoryW: list[dict[str, dict[str, dict[int, int]]]], max_history: int):
    for h_idx in range(max_history):
        W = HistoryW[h_idx]

        for inp_symbol, s_indeces in W.items():
            symbol_stat_sum = 0

            for out_symbol, index_stat in s_indeces.items():
                for index, idx_stat in index_stat.items():
                    symbol_stat_sum += idx_stat

            for out_symbol, index_stat in s_indeces.items():
                for index, idx_stat in index_stat.items():
                    W[inp_symbol][out_symbol][index] = idx_stat / symbol_stat_sum
    
    return HistoryW
        
HistoryW = to_probability(HistoryW, max_history=max_history_L1)

for h_idx in range(max_history_L1):
    for wk, wv in HistoryW[h_idx].items():
        print(wk, wv)

c0 {'h': {0: 1.0}}
h0 {'a': {0: 1.0}}
a0 {'p': {0: 1.0}}
p0 {'t': {0: 1.0}}
t0 {'e': {0: 1.0}}
e0 {'r': {0: 0.4}, 'c': {17: 0.1}, ' ': {30: 0.2, 33: 0.1}, 'l': {21: 0.1, 17: 0.1}}
r0 {' ': {0: 0.75}, 'e': {44: 0.25}}
 0 {'i': {0: 0.4}, 'f': {5: 0.2}, 'b': {14: 0.2}, 't': {51: 0.2}}
i0 {'n': {0: 0.5}, 't': {54: 0.5}}
n0 {' ': {1: 1.0}}
 1 {'w': {0: 0.5}, 'a': {18: 0.25}, 'y': {11: 0.25}}
w0 {'h': {1: 0.5}, 'i': {10: 0.5}}
h1 {'i': {1: 1.0}}
i1 {'c': {1: 1.0}}
c1 {'h': {2: 1.0}}
h2 {' ': {2: 1.0}}
 2 {'w': {1: 0.3333333333333333}, 'm': {9: 0.3333333333333333}, 's': {30: 0.3333333333333333}}
w1 {'e': {1: 1.0}}
e1 {' ': {3: 0.2, 37: 0.4}, 's': {22: 0.4}}
 3 {'a': {1: 0.3333333333333333}, 'o': {25: 0.3333333333333333}, 'h': {37: 0.3333333333333333}}
a1 {'r': {1: 0.5}, 'n': {1: 0.5}}
r1 {'e': {2: 1.0}}
e2 {' ': {4: 0.5}, 'l': {14: 0.5}}
 4 {'i': {2: 0.3333333333333333}, 'a': {1: 0.3333333333333333}, 't': {20: 0.3333333333333333}}
i2 {'n': {1: 1.0}}
n1 {'t': {1: 0.5}, 'd': {11: 0.5}}
t1 {'r':

In [296]:
def predict(input_str: str, 
            HistoryW: list[dict[str, dict[str, dict[int, int]]]], 
            max_history = 4,
            max_index = 4,):
    err = 0
    TF = []
    AL = []

    history_indices = []
    history_indices.append([x for x in range(max_index)])

    for input_idx, input in enumerate(input_str[:-1]):
        HO: dict[str, dict[int, int]] = {}
        HO_cnt: dict[str, dict[int, int]] = {}

        itr_max_history = 0

        for h_idx in range(max_history):
            # print(f'{h_idx=}')

            inp_idx = input_idx - h_idx
            if inp_idx < 0:
                break

            itr_max_history += 1
            # print(f'{h_idx=} {inp_idx=}')
            W = HistoryW[h_idx]
            inp = input_str[inp_idx]
            indices = history_indices[h_idx]

            key_I = inp + str(indices[0])
            O = W.get(key_I, {})
            # print(f'{O=}')
            # print()

            for index in indices[1:]:
                key_I = inp + str(index)

                index_O = W.get(key_I, {})
                # print(f'{index_O=}')
                # print()

                for key, val in index_O.items():
                    O.setdefault(key, {})
                    O[key].update(val)
            
            # print(f'{O=}')
            # print()
            
            for key_O, val_O in O.items():
                HO.setdefault(key_O, {})
                HO_cnt.setdefault(key_O, {})
                
                for key_index, val_index in val_O.items():
                    HO[key_O].setdefault(key_index, 0)
                    HO_cnt[key_O].setdefault(key_index, 0)

                    HO[key_O][key_index] += val_index
                    HO_cnt[key_O][key_index] += 1

        # print(f'{HO=}')
        # print(f'{HO_cnt=}')
        # print()

        length = 0
        for v in HO.values():
            length += len(v)

        max_arr = []
        for v in HO.values():
            col_max = max(v, key=v.get)
            max_arr.append(col_max)
        
        max_arr = np.array(max_arr)
        # tf = np.mean(np.abs(max_arr - max_arr[np.newaxis].T))

        tf = length
        # tf = len(HO)

        TF.append(tf)

        # max by cnt
        # max_symbol = 'a'
        # max_symbol_index = 0
        # max_val = 0
        # for key, val in HO_cnt.items():
        #     max_idx = max(val, key=val.get)
        #     # HO_cnt[key] = {max_idx: val[max_idx]}

        #     if val[max_idx] > max_val: # 
        #         max_val = val[max_idx]
        #         max_symbol_index = max_idx
        #         max_symbol = key
        # print(f'{max_symbol=}')
        # max by val
        max_symbol = 'a'
        max_symbol_index = 0
        max_val = 0
        # win_cnt = 0
        for key, val in HO.items():
            for index, index_stat in val.items():
                index_cnt = HO_cnt[key][index]
                stat = pow(0.1, (itr_max_history - index_cnt)) * index_stat
                # stat = -0.5 * (itr_max_history - index_cnt) + index_stat

                HO[key][index] = stat

            max_idx = max(val, key=val.get)
            HO[key] = {max_idx: val[max_idx]}

            # max_cnt = HO_cnt[key][max_idx]

            if val[max_idx] > max_val: # and max_cnt >= max_his:
                # print(f'{key=} {val[max_idx]=} {max_cnt=}')
                max_val = val[max_idx]
                max_symbol_index = max_idx
                max_symbol = key
                # win_cnt = max_cnt

        # print(f'{HO=}')
        next_inp = input_str[input_idx + 1]
        print(f'{max_symbol=}', f'{next_inp=} {max_val=} {itr_max_history=} {HO=}', max_symbol_index, max_val)
        # print('')

        # anomaly
        if max_symbol == next_inp:
            AL.append(0)
        else:
            ni_v = HO.get(next_inp, 0)
            if ni_v == 0:
                AL.append(100)
            else:
                max_ni = max(ni_v, key=ni_v.get)
                AL.append(abs(ni_v[max_ni] - max_val))

        new_indices = [max_symbol_index]

        # err
        if max_symbol != next_inp:
            err += 1

            index_stats = HO.get(next_inp, 0)
            
            if index_stats == 0:
                new_indices = [x for x in range(max_index)]
                print(f'{new_indices=}')
            else:
                max_symbol_index = list(index_stats.keys())[0]

                new_indices = [max_symbol_index]
        
        # recurtion
        history_indices.insert(0, new_indices)
        if len(history_indices) > max_history:
            history_indices = history_indices[:-1]

    TF.append(0)
    AL.append(0)
    return err, TF, AL

err_L1, TF_L1, AL_L1 = predict(input_str, HistoryW, max_index=max_index_L1, max_history=max_history_L1)
# err_L1, TF_L1_no, AL_L1_no = predict(input_str, HistoryW, max_index=max_index_L1, max_history=max_history_L1)

print(err_L1, err_L1 / (len(input_str) / 100))

max_symbol='h' next_inp='h' max_val=1.0 itr_max_history=1 HO={'h': {0: 1.0}, 'e': {3: 1.0}, 'o': {6: 1.0}, 'k': {0: 1.0}, 'a': {32: 1.0}, 'l': {12: 0.4}, 'r': {9: 0.1}, 'i': {49: 0.2}} 0 1.0
max_symbol='a' next_inp='a' max_val=2.0 itr_max_history=2 HO={'a': {0: 2.0}, ' ': {2: 0.1}, 'd': {1: 0.1}, 'm': {1: 0.1}, 'r': {24: 0.1}, 'i': {52: 0.05}, 'u': {5: 0.1}, 'f': {17: 0.0058823529411764705}, 'l': {4: 0.1}, 'n': {32: 0.1}, 'e': {45: 0.006666666666666667}} 0 2.0
max_symbol='p' next_inp='p' max_val=3.0 itr_max_history=3 HO={'p': {0: 3.0}, 'w': {1: 0.010000000000000002}, ' ': {5: 0.010000000000000002}, 'i': {8: 0.010000000000000002}, 'o': {10: 0.0010000000000000002}, 'e': {1: 0.0020000000000000005}, 'm': {25: 0.004000000000000001}, 'y': {14: 0.010000000000000002}, 'r': {9: 0.0005882352941176471}, 'u': {19: 0.0006666666666666668}, 'l': {5: 0.010000000000000002}, "'": {1: 0.010000000000000002}, 's': {6: 0.010000000000000002}, 'c': {5: 0.0010000000000000002}, 'a': {8: 0.0006666666666666668}, 

In [297]:
def get_word_stats(input_str: str | list, TF: list, threshold=0.0):
    buffer: list = [input_str[0]]
    WordStats: dict[str, int] = {}
    WordIndex: dict[str, int] = {}
    next_wrd_idx = 0

    NextLayerOut = []
    DownstreamIndex = {}

    prev_tf = TF[0]

    for inp_idx, inp in enumerate(input_str):
        if inp_idx <= 0 and inp_idx >= len(input_str) - 1:
            continue

        # if TF[inp_idx] - prev_tf > 0.0: # and abs(TF[inp_idx] - prev_tf) > 0.2:
        # and TF[inp_idx] > threshold:
        if TF[inp_idx] > prev_tf and TF[inp_idx] > TF[inp_idx + 1]:
            word = ''.join(buffer)

            WordStats.setdefault(word, 0)
            WordStats[word] += 1

            if not WordIndex.get(word):
                WordIndex.setdefault(word, next_wrd_idx)
                next_wrd_idx += 1

            wrd_idx = WordIndex.get(word)
            # NextLayerOut.append(str(wrd_idx))
            NextLayerOut.append(word)

            DownstreamIndex.setdefault(inp_idx, 1)

            buffer = [inp]
            prev_tf = TF[inp_idx]

            continue

        TF[inp_idx] = 0

        buffer.append(inp)
        prev_tf = TF[inp_idx]

    # sort
    WordStats = dict(sorted(WordStats.items(), key=lambda item: item[1], reverse=True))

    NextLayerOut.append(str(next_wrd_idx))
    return WordStats, WordIndex, NextLayerOut, DownstreamIndex


TF_L1 = np.array(TF_L1, dtype='float64')
AL_L1 = np.array(AL_L1, dtype='float64')
TF_L1 /= np.max(TF_L1)
AL_L1 /= np.max(AL_L1)
TF_L1 += AL_L1

TF_max_coef = 0.4

# TF_L1[np.where(TF_L1 < np.mean(TF_L1))] = 0
# TF_1 = TF_L1 - np.pad(TF_L1, (1, 0))[:-1]
# TF_2 = TF_L1 - np.pad(TF_L1, (0, 1))[1:]
# TF_L1 = TF_1 + TF_2

# TF_L1[np.where(TF_L1 < 0)] = 0
# TF_L1[np.where(TF_L1 < TF_max_coef)] = 0
TF_L1 = TF_L1.tolist()

WordStats_L1, WordIndex_L1, NextLayerOut_L1, DownstreamIndex_L1 = get_word_stats(input_str=input_str,
                                                                                 TF=TF_L1, 
                                                                                 threshold=0.0, )
print(len(WordStats_L1))
mean_WS = np.mean(np.array(list(WordStats_L1.values())))
print(f'{mean_WS=}')
WS_len = 0
for key, val in WordStats_L1.items():
    # if len(key.strip()) > 1 and val >= mean_WS:
    if val >= mean_WS:
        WS_len += 1
    print(key, val)
print(f'{WS_len=}')

print(f'{NextLayerOut_L1=}')
print(f'{len(NextLayerOut_L1)=}')

print(f'{WordIndex_L1=}')

print(f'{DownstreamIndex_L1=}')


791
mean_WS=2.225031605562579
 t 37
 a 36
 s 30
 b 29
he 25
 h 23
 w 21
 i 19
 he 19
nd 18
in 15
 c 14
th 14
e  14
s  13
on 12
 th 12
an 12
at 11
ou 11
me 10
ng 10
st 10
 g 10
g  10
 l 10
 f 10
is 9
d  9
 y 9
and 9
 of 9
t  9
er 9
ad 9
n  9
re 8
 to 8
 n 8
om 8
 it 8
id 8
aid 8
 r 8
or 7
ed 7
 the 7
o  7
al 7
ob 7
 so 6
 be 6
ow 6
of 6
en 6
 p 6
es 6
ha 6
li 6
oh  6
 d 6
ee 6
hi 6
 o 5
hat 5
ai 5
to 5
the 5
sa 5
 wh 5
ly 5
a  5
im 5
se 5
 m 5
 and 5
as  5
ro 4
r  4
bin 4
he  4
ng  4
oh 4
you 4
rs 4
her 4
 ro 4
et 4
ve 4
 la 4
as 4
 in 4
 po 4
nk 4
all 4
ing 4
 cl 4
ne 4
is  3
hr 3
top 3
 i  3
ou  3
 sa 3
ut 3
wi 3
nn 3
er  3
 said 3
it 3
ooh 3
f  3
so 3
ie 3
i  3
of  3
 co 3
nie 3
n a 3
 as 3
n't 3
 gr 3
ace 3
le 3
zi 3
 his 3
no 3
 bu 3
at i 3
lo 3
imb 3
un 3
ust 3
y  3
ho 3
ed  3
h  3
cr 3
in  3
 ch 3
loo 3
innie 2
rd 2
ow  2
ind 2
ay 2
ing  2
dow 2
op 2
nd  2
re  2
hen 2
rst 2
 hi 2
na 2
ju 2
oi 2
ca 2
on't  2
on't 2
 do 2
use  2
 is  2
pla 2
et  2
ik 2
es  2
 qu 2
ly  2
ab 2
ry  2


In [298]:
def downstream_train(input: list, next_layer_out: list, downstream_index: dict[int, int]):
    DSStats = {}

    ds_idx = 1
    ds_inp = next_layer_out[0]

    for inp_idx, inp in enumerate(input[:-1]):
        has_ds_input = downstream_index.get(inp_idx)
        if has_ds_input:
            ds_inp = next_layer_out[ds_idx]
            ds_idx += 1

        ds_key = ds_inp + ':' + inp
        DSStats.setdefault(ds_key, 0)
        DSStats[ds_key] += 1

    return DSStats


DSStats = downstream_train(input=input_str,
                           next_layer_out=NextLayerOut_L1,
                           downstream_index=DownstreamIndex_L1,)

for wk, wv in DSStats.items():
    print(wk, wv)

ccha:c 1
ccha:h 1
ccha:a 1
pter in:p 1
pter in:t 1
pter in:e 1
pter in:r 1
pter in:  1
pter in:i 1
pter in:n 1
 which:  1
 which:w 1
 which:h 2
 which:i 1
 which:c 1
 w:  21
 w:w 21
e a:e 1
e a:  1
e a:a 1
re:r 8
re:e 8
 i:  19
 i:i 19
nt:n 1
nt:t 1
ro:r 4
ro:o 4
duced:d 2
duced:u 1
duced:c 1
duced:e 1
 to:  8
 to:t 8
 to:o 8
innie:i 4
innie:n 4
innie:e 2
 the :  2
 the :t 1
 the :h 1
 the :e 1
pooh a:p 1
pooh a:o 2
pooh a:h 1
pooh a:  1
pooh a:a 1
nd:n 18
nd:d 18
 so:  6
 so:s 6
 so:o 6
me:m 10
me:e 10
 b:  29
 b:b 29
ees a:e 2
ees a:s 1
ees a:  1
ees a:a 1
nd the st:n 1
nd the st:d 1
nd the st:  2
nd the st:t 2
nd the st:h 1
nd the st:e 1
nd the st:s 1
or:o 7
or:r 7
ies:i 1
ies:e 1
ies:s 1
 be:  6
 be:b 6
 be:e 6
gin:g 1
gin:i 1
gin:n 1
 here :  2
 here :h 1
 here :e 2
 here :r 1
is :i 3
is :s 3
is :  3
ed:e 7
ed:d 7
wa:w 1
wa:a 1
rd:r 2
rd:d 2
ear:e 1
ear:a 1
ear:r 1
 c:  14
 c:c 14
omi:o 1
omi:m 1
omi:i 1
ng:n 10
ng:g 10
 downsta:  1
 downsta:d 1
 downsta:o 1
 downsta:w 1
 downsta:

In [299]:
def downstream_predict(input_str: str, 
            HistoryW: list[dict[str, dict[str, dict[int, int]]]], 
            upstream_inp: dict[int, list],
            DSStats: dict[str, int],
            ds_input: list,
            max_history = 4,
            max_index = 4,):
    err = 0
    TF = []

    history_indices = []
    history_indices.append([x for x in range(max_index)])

    ds_idx = 1
    ds_inp = ds_input[0]

    for input_idx, input in enumerate(input_str[:-1]):
        HO: dict[str, dict[int, int]] = {}

        for h_idx in range(max_history):
            inp_idx = input_idx - h_idx
            if inp_idx < 0:
                break
            # print(f'{h_idx=} {inp_idx=}')
            W = HistoryW[h_idx]
            inp = input_str[inp_idx]
            indices = history_indices[h_idx]

            key_I = inp + str(indices[0])
            # print(f'{key_I=}')
            O = W.get(key_I, {})
            # print(f'{O=}')
            # print()

            for index in indices[1:]:
                key_I = inp + str(index)
                # print(f'{key_I=}')

                index_O = W.get(key_I, {})
                # print(f'{index_O=}')
                # print()

                for key, val in index_O.items():
                    O.setdefault(key, {})
                    O[key].update(val)
            
            # print(f'{O=}')
            # print()
            
            for key_O, val_O in O.items():
                HO.setdefault(key_O, {})
                
                for key_index, val_index in val_O.items():
                    HO[key_O].setdefault(key_index, 0)

                    HO[key_O][key_index] += val_index

        # print(f'{HO=}')
        # print()

        length = 0
        for v in HO.values():
            length += len(v)

        # tf = length
        tf = len(HO)

        TF.append(tf)

        # ds input
        has_ds_input = upstream_inp.get(input_idx + 1)
        if has_ds_input:
            ds_inp = ds_input[ds_idx]
            ds_idx += 1

        # max symbol
        max_symbol = 'a'
        max_symbol_index = 0
        max_val = 0
        for key, val in HO.items():
            max_idx = max(val, key=val.get)
            HO[key] = {max_idx: val[max_idx]}
            max_idx_val = val[max_idx]

            # ds predict
            ds_key = ds_inp + ':' + key
            ds_stats = DSStats.get(ds_key)
            # if ds_stats:
            #     max_idx_val += ds_stats

            if max_idx_val > max_val and ds_stats:
                max_val = max_idx_val
                max_symbol_index = max_idx
                max_symbol = key

        # print(f'{HO=}')
        next_inp = input_str[input_idx + 1]
        print(f'{max_symbol=}', f'{next_inp=} {ds_inp=} {HO=}', max_symbol_index, max_val)

        # print(f'{O.get(max_symbol).keys()=}')
        new_indices = [max_symbol_index]

        if O.get(max_symbol):
            new_indices = list(O.get(max_symbol).keys())            

        # err
        if max_symbol != next_inp:
            err += 1

            index_stats = HO.get(next_inp, 0)
            
            if index_stats == 0:
                new_indices = [x for x in range(max_index)]
                print(f'{new_indices=}')
            else:
                max_symbol_index = list(index_stats.keys())[0]

                new_indices = [max_symbol_index]
        
        # recurtion
        history_indices.insert(0, new_indices)
        if len(history_indices) > max_history:
            history_indices = history_indices[:-1]

    return err, TF

HistoryW, HistoryHW, IDX = predict_train(input_str, letters, max_history=max_history_L1_ds, max_index=max_index_L1)

# for h_idx in range(max_history_L1_ds):
#     print(f'{h_idx=}')
#     for wk, wv in HistoryW[h_idx].items():
#         print(wk, wv)

err_L1_ds, TF_L1_ds = downstream_predict(input_str=input_str, 
                                        HistoryW=HistoryW, 
                                        upstream_inp=DownstreamIndex_L1,
                                        DSStats=DSStats,
                                        ds_input=NextLayerOut_L1,
                                        max_history=max_history_L1_ds,
                                        max_index=max_index_L1, )

print(f'{err_L1=}', err_L1 / (len(input_str) / 100))
print(f'{err_L1_ds=}', err_L1_ds / (len(input_str) / 100))

max_symbol='h' next_inp='h' ds_inp='ccha' HO={'h': {6: 6}, 'e': {54: 2}, 'o': {6: 2}, 'l': {17: 2}, 'k': {4: 2}, 'a': {40: 3}, 'r': {20: 2}, 'i': {58: 1}} 6 6
max_symbol='a' next_inp='a' ds_inp='ccha' HO={'a': {46: 9}, ' ': {20: 8}, 'e': {13: 32}, 'o': {28: 2}, 'i': {5: 11}, 'r': {19: 8}, 'd': {1: 1}, 'm': {1: 3}, 'u': {17: 4}, 'n': {34: 1}, 'l': {7: 1}, 'f': {14: 1}} 46 9
max_symbol='n' next_inp='p' ds_inp='pter in' HO={'p': {0: 3}, 'd': {27: 8}, 'l': {8: 11}, 't': {54: 9}, 'k': {10: 2}, 'u': {17: 4}, 'n': {6: 16}, ' ': {15: 8}, 'i': {46: 7}, 'c': {18: 3}, 'b': {1: 4}, 's': {52: 9}, 'w': {25: 3}, 'g': {13: 1}, 'r': {38: 4}, 'h': {26: 1}, 'm': {21: 6}, 'y': {15: 2}, 'o': {27: 3}, 'a': {22: 3}, "'": {7: 1}, 'v': {1: 1}, 'e': {14: 3}} 6 16
max_symbol=' ' next_inp='t' ds_inp='pter in' HO={'t': {0: 4}, 'y': {6: 1}, 'l': {18: 8}, ' ': {15: 14}, 's': {21: 14}, 'd': {14: 8}, 'v': {1: 1}, 'h': {47: 3}, 'n': {58: 2}, 'c': {17: 4}, 'k': {8: 3}, 'e': {54: 3}, 'o': {28: 4}, 'f': {14: 2}, 'b': {21: